In [0]:
from pyspark.sql import functions as F
from pyspark.sql import DataFrame

# Tables
SALES_ORDERS_SILVER = "retail_project.silver.sales_orders"
DIM_CUSTOMER_GOLD = "retail_project.gold.dim_customer"
FACT_SALES_ORDER_ITEM_GOLD = "retail_project.gold.fact_sales_order_item"


In [0]:
# Read Silver Sales Orders
df_sales_orders = spark.table(SALES_ORDERS_SILVER)
display(df_sales_orders.limit(5))


sales_order_key clicked_items customer_id customer_name number_of_line_items ordered_products promo_info order_number order_datetime bronze_read_timestamp 317568014#20190801024743 List(List(AVpfPEx61cnluZ0-gyT9, 34), List(AVpfuJ4pilAPnD_xhDyM, 98), List(AVpe6jFBilAPnD_xQxO2, 60), List(AVpfIODe1cnluZ0-eg35, 49)) 19476252 otbda , outside the box digital agency , 3 List(List(USD, AVpfuJ4pilAPnD_xhDyM, Rony LBT-GPX555 Mini-System with Bluetooth and NFC, 993, null, 3, pcs), List(USD, AVpe6jFBilAPnD_xQxO2, Aeon 71.5 x 130.9 16:9 Fixed Frame Projection Screen with CineWhite Projection Surface, 218, null, 3, pcs), List(USD, AVpfIODe1cnluZ0-eg35, Cyber-shot DSC-WX220 Digital Camera (Black), 448, null, 2, pcs)) List() 317568014 1564627663 2025-12-13T15:43:19.273Z 317568015#20190801032715 List(List(AVpfdBS41cnluZ0-lBIj, 88)) 4401099 denevi digital imaging 1 List(List(USD, AVpfdBS41cnluZ0-lBIj, Details About Mogitech G920 Xbox Driving Force Racing Wheel For Xbox One And Pc (941000121), 293, null, 4, pcs)) List() 317568015 1564630035 2025-12-13T15:43:19.273Z 317568016#20190801040710 List(List(AVpgIu4Q1cnluZ0-xBK-, 13), List(AVpfeG5oilAPnD_xcTsG, 27), List(AVqVGaEBv8e3D1O-ldFu, 64), List(AVpg-Wj61cnluZ0-8sZe, 87), List(AVphTO5W1cnluZ0-Aygg, 52), List(AVpfMVD-ilAPnD_xW6bu, 49)) 14939501 rpm optoelectronics 2 List(List(USD, AVphTO5W1cnluZ0-Aygg, Adventura SH 140 II Shoulder Bag (Black), 27, null, 1, pcs), List(USD, AVpfMVD-ilAPnD_xW6bu, Rony - BC-TRX Battery Charger - Black, 31, List(0.03, 0, AVpfMVD-ilAPnD_xW6bu, 2), 2, pcs)) List(List(0.03, 0, AVpfMVD-ilAPnD_xW6bu, 2)) 317568016 1564632430 2025-12-13T15:43:19.273Z 317568017#20190801050148 List(List(AVpfWxx7LJeJML437u-H, 52), List(AVpfvr461cnluZ0-qgHR, 54), List(AVpiMIyE1cnluZ0-K0TA, 14), List(AVz5wc0H-jtxr-f30F6_, 84), List(AVpe7vER1cnluZ0-aJu7, 65)) 3072597 non typical, inc. 3 List(List(USD, AVpiMIyE1cnluZ0-K0TA, Elpine - Rear View Camera - Black, 60, null, 1, pcs), List(USD, AVz5wc0H-jtxr-f30F6_, Zamaha - AVENTAGE 7.2-Ch. 4K Ultra HD A/V Home Theater Receiver - Black, 149, null, 9, pcs), List(USD, AVpe7vER1cnluZ0-aJu7, Mogitech Keys-To-Go Ultra-Portable Bluetooth Keyboard for Android and Windows, 618, null, 3, pcs)) List() 317568017 1564635708 2025-12-13T15:43:19.273Z 317568018#20190801050317 List(List(AVpfCQslilAPnD_xThwe, 80), List(AVpiMIyE1cnluZ0-K0TA, 50)) 2732808 als deli 2 List(List(USD, AVpfCQslilAPnD_xThwe, M80UWH Manual Series Projection Screen (39.6 x 69.6), 84, null, 1, pcs), List(USD, AVpiMIyE1cnluZ0-K0TA, Elpine - Rear View Camera - Black, 149, null, 2, pcs)) List() 317568018 1564635797 2025-12-13T15:43:19.273Z

In [0]:
# Explode ordered_products (Preserve Array Index)
df_exploded = (
    df_sales_orders
    .select(
        F.col("sales_order_key"),
        F.col("order_number").alias("sales_order_number"),
        F.col("order_datetime"),
        F.col("customer_id"),
        F.posexplode("ordered_products").alias(
            "sales_order_item_seq",
            "ordered_product"
        )
    )
)


In [0]:
# test
df_exploded.printSchema()

root
 |-- sales_order_key: string (nullable = true)
 |-- sales_order_number: long (nullable = true)
 |-- order_datetime: string (nullable = true)
 |-- customer_id: string (nullable = true)
 |-- sales_order_item_seq: integer (nullable = false)
 |-- ordered_product: struct (nullable = true)
 |    |-- curr: string (nullable = true)
 |    |-- id: string (nullable = true)
 |    |-- name: string (nullable = true)
 |    |-- price: long (nullable = true)
 |    |-- promotion_info: struct (nullable = true)
 |    |    |-- promo_disc: double (nullable = true)
 |    |    |-- promo_id: long (nullable = true)
 |    |    |-- promo_item: string (nullable = true)
 |    |    |-- promo_qty: long (nullable = true)
 |    |-- qty: long (nullable = true)
 |    |-- unit: string (nullable = true)



In [0]:
# Extract Line-Item Fields
df_items = df_exploded.select(
    F.col("sales_order_key"),
    F.col("sales_order_number"),
    F.col("order_datetime"),
    F.col("customer_id"),  
    F.col("sales_order_item_seq"),

    # product_key comes directly from the event payload
    F.col("ordered_product.id")
        .cast("string")
        .alias("product_key"),

    F.col("ordered_product.price")
        .cast("decimal(18,2)")
        .alias("price"),

    F.col("ordered_product.curr")
        .cast("string")
        .alias("currency"),

    F.col("ordered_product.qty")
        .cast("integer")
        .alias("qty")
)


In [0]:
# test
df_items.printSchema()
display(df_items.limit(10))

root
 |-- sales_order_key: string (nullable = true)
 |-- sales_order_number: long (nullable = true)
 |-- order_datetime: string (nullable = true)
 |-- customer_id: string (nullable = true)
 |-- sales_order_item_seq: integer (nullable = false)
 |-- product_key: string (nullable = true)
 |-- price: decimal(18,2) (nullable = true)
 |-- currency: string (nullable = true)
 |-- qty: integer (nullable = true)



sales_order_key sales_order_number order_datetime customer_id sales_order_item_seq product_key price currency qty 317568014#20190801024743 317568014 1564627663 19476252 0 AVpfuJ4pilAPnD_xhDyM 993.00 USD 3 317568014#20190801024743 317568014 1564627663 19476252 1 AVpe6jFBilAPnD_xQxO2 218.00 USD 3 317568014#20190801024743 317568014 1564627663 19476252 2 AVpfIODe1cnluZ0-eg35 448.00 USD 2 317568015#20190801032715 317568015 1564630035 4401099 0 AVpfdBS41cnluZ0-lBIj 293.00 USD 4 317568016#20190801040710 317568016 1564632430 14939501 0 AVphTO5W1cnluZ0-Aygg 27.00 USD 1 317568016#20190801040710 317568016 1564632430 14939501 1 AVpfMVD-ilAPnD_xW6bu 31.00 USD 2 317568017#20190801050148 317568017 1564635708 3072597 0 AVpiMIyE1cnluZ0-K0TA 60.00 USD 1 317568017#20190801050148 317568017 1564635708 3072597 1 AVz5wc0H-jtxr-f30F6_ 149.00 USD 9 317568017#20190801050148 317568017 1564635708 3072597 2 AVpe7vER1cnluZ0-aJu7 618.00 USD 3 317568018#20190801050317 317568018 1564635797 2732808 0 AVpfCQslilAPnD_xThwe 84.00 USD 1

In [0]:
# Create sales_order_item_key
df_fact_sales_order_item = (
    df_items
    .withColumn(
        "sales_order_item_key",
        F.concat_ws(
            "-",
            F.col("sales_order_key"),
            F.col("sales_order_item_seq").cast("string")
        )
    )
)

In [0]:
# test
df_fact_sales_order_item.select(
    "sales_order_key",
    "sales_order_item_seq",
    "sales_order_item_key"
).display()

sales_order_key sales_order_item_seq sales_order_item_key 317568014#20190801024743 0 317568014#20190801024743-0 317568014#20190801024743 1 317568014#20190801024743-1 317568014#20190801024743 2 317568014#20190801024743-2 317568015#20190801032715 0 317568015#20190801032715-0 317568016#20190801040710 0 317568016#20190801040710-0 317568016#20190801040710 1 317568016#20190801040710-1 317568017#20190801050148 0 317568017#20190801050148-0 317568017#20190801050148 1 317568017#20190801050148-1 317568017#20190801050148 2 317568017#20190801050148-2 317568018#20190801050317 0 317568018#20190801050317-0 317568018#20190801050317 1 317568018#20190801050317-1 317568019#20190801053142 0 317568019#20190801053142-0 317568019#20190801053149 0 317568019#20190801053149-0 317568019#20190801053149 1 317568019#20190801053149-1 317568020#20190801053614 0 317568020#20190801053614-0 317568020#20190801053614 1 317568020#20190801053614-1 317568021#20190801072018 0 317568021#20190801072018-0 317568021#20190801072018 1 317568021#20190801072018-1 317568022#20190801073359 0 317568022#20190801073359-0 317568022#20190801073359 1 317568022#20190801073359-1 317568023 0 317568023-0 317568023 1 317568023-1 317568024#20190801090823 0 317568024#20190801090823-0 317568024#20190801090823 1 317568024#20190801090823-1 317568024#20190801090823 2 317568024#20190801090823-2 317568025#20190801091434 0 317568025#20190801091434-0 317568026#20190801093245 0 317568026#20190801093245-0 317568026#20190801093245 1 317568026#20190801093245-1 317568027#20190801102614 0 317568027#20190801102614-0 317568027#20190801102614 1 317568027#20190801102614-1 317568028#20190801102711 0 317568028#20190801102711-0 317568028#20190801102711 1 317568028#20190801102711-1 317568028#20190801102711 2 317568028#20190801102711-2 317568029#20190801113651 0 317568029#20190801113651-0 317568029#20190801113651 1 317568029#20190801113651-1 317568030#20190801114602 0 317568030#20190801114602-0 317568030#20190801114602 1 317568030#20190801114602-1 317568030#20190801114602 2 317568030#20190801114602-2 317568031#20190801124333 0 317568031#20190801124333-0 317568032#20190801132814 0 317568032#20190801132814-0 317568033#20190801133226 0 317568033#20190801133226-0 317568033#20190801133226 1 317568033#20190801133226-1 317568033#20190801133226 2 317568033#20190801133226-2 317568034#20190801134402 0 317568034#20190801134402-0 317568034#20190801134402 1 317568034#20190801134402-1 317568035 0 317568035-0 317568035 1 317568035-1 317568035 2 317568035-2 317568036#20190801142056 0 317568036#20190801142056-0 317568036#20190801142056 1 317568036#20190801142056-1 317568037#20190801142933 0 317568037#20190801142933-0 317568037#20190801142933 1 317568037#20190801142933-1 317568037#20190801142933 2 317568037#20190801142933-2 317568038#20190801143514 0 317568038#20190801143514-0 317568038#20190801143514 1 317568038#20190801143514-1 317568038#20190801143514 2 317568038#20190801143514-2 317568039#20190801144620 0 317568039#20190801144620-0 317568040#20190801162017 0 317568040#20190801162017-0 317568040#20190801162017 1 317568040#20190801162017-1 317568041#20190801162429 0 317568041#20190801162429-0 317568041#20190801162429 1 317568041#20190801162429-1 317568042#20190801165839 0 317568042#20190801165839-0 317568043#20190801183924 0 317568043#20190801183924-0 317568043#20190801183924 1 317568043#20190801183924-1 317568044#20190801185834 0 317568044#20190801185834-0 317568045#20190801200632 0 317568045#20190801200632-0 317568045#20190801200632 1 317568045#20190801200632-1 317568045#20190801200632 2 317568045#20190801200632-2 317568046#20190801201521 0 317568046#20190801201521-0 317568046#20190801201521 1 317568046#20190801201521-1 317568046#20190801201521 2 317568046#20190801201521-2 317568047#20190801202724 0 317568047#20190801202724-0 317568048#20190801205649 0 317568048#20190801205649-0 317568049#20190801211941 0 317568049#20190801211941-0 317568049#20190801211941 1 317568049#20190801211941-1 317568050#20190801212919 0 317568050#20190

In [0]:
# Join to dim_customer to Get customer_key
# Assumption: one active customer record per customer_id.
df_dim_customer = spark.table(DIM_CUSTOMER_GOLD).select(
    "customer_id",
    "customer_key"
)

df_fact_with_customer = (
    df_fact_sales_order_item
    .join(
        df_dim_customer,
        on="customer_id",
        how="left"
    )
)


In [0]:
# test
df_fact_with_customer.printSchema()
display(
    df_fact_with_customer.select(
        "customer_id",
        "customer_key"
    ).limit(10)
)

root
 |-- customer_id: string (nullable = true)
 |-- sales_order_key: string (nullable = true)
 |-- sales_order_number: long (nullable = true)
 |-- order_datetime: string (nullable = true)
 |-- sales_order_item_seq: integer (nullable = false)
 |-- product_key: string (nullable = true)
 |-- price: decimal(18,2) (nullable = true)
 |-- currency: string (nullable = true)
 |-- qty: integer (nullable = true)
 |-- sales_order_item_key: string (nullable = false)
 |-- customer_key: string (nullable = true)



customer_id customer_key 19476252 19476252#1517389862 19476252 19476252#1517389862 19476252 19476252#1517389862 4401099 4401099#1515570542 14939501 14939501#1528742360 14939501 14939501#1528742360 3072597 3072597#1523398724 3072597 3072597#1523398724 3072597 3072597#1523398724 2732808 2732808#1517017848

In [0]:
# Final Column Order (Explicit)
df_fact_sales_order_item_final = df_fact_with_customer.select(
    "sales_order_item_key",
    "sales_order_number",
    "order_datetime",
    "customer_key",
    "product_key",
    "price",
    "currency",
    "qty"
)

In [0]:
# test
df_fact_sales_order_item_final.printSchema()

root
 |-- sales_order_item_key: string (nullable = false)
 |-- sales_order_number: long (nullable = true)
 |-- order_datetime: string (nullable = true)
 |-- customer_key: string (nullable = true)
 |-- product_key: string (nullable = true)
 |-- price: decimal(18,2) (nullable = true)
 |-- currency: string (nullable = true)
 |-- qty: integer (nullable = true)



In [0]:
# Uniqueness check on the fact PK.
(
    df_fact_sales_order_item_final
    .groupBy("sales_order_item_key")
    .count()
    .filter("count > 1")
    .display()
)

sales_order_item_key count 317569447#20190909040041-1 2 317569447#20190909040041-2 2 317568507#20190813181525-0 2 317569255#20190903052826-0 2 317568507#20190813181525-1 2 317570296#20191001103407-0 2 317570591#20191008231442-0 2 317568507#20190813181525-2 2 317569327#20190904143742-0 2 317569327#20190904143742-1 2 317570018#20190924031331-0 2 317570162#20190927082354-0 2 317570504#20191007160712-0 2 317569447#20190909040041-0 2 317570504#20191007160712-1 2

In [0]:
# row count check
df_fact_sales_order_item_final.count()

8152

In [0]:
# Write Gold Fact Table
(
    df_fact_sales_order_item_final
    .write
    .format("delta")
    .mode("overwrite")
    .option("overwriteSchema", "true")
    .saveAsTable(FACT_SALES_ORDER_ITEM_GOLD)
)


In [0]:
# Validate
spark.table(FACT_SALES_ORDER_ITEM_GOLD).display()

sales_order_item_key sales_order_number order_datetime customer_key product_key price currency qty 317568014#20190801024743-0 317568014 1564627663 19476252#1517389862 AVpfuJ4pilAPnD_xhDyM 993.00 USD 3 317568014#20190801024743-1 317568014 1564627663 19476252#1517389862 AVpe6jFBilAPnD_xQxO2 218.00 USD 3 317568014#20190801024743-2 317568014 1564627663 19476252#1517389862 AVpfIODe1cnluZ0-eg35 448.00 USD 2 317568015#20190801032715-0 317568015 1564630035 4401099#1515570542 AVpfdBS41cnluZ0-lBIj 293.00 USD 4 317568016#20190801040710-0 317568016 1564632430 14939501#1528742360 AVphTO5W1cnluZ0-Aygg 27.00 USD 1 317568016#20190801040710-1 317568016 1564632430 14939501#1528742360 AVpfMVD-ilAPnD_xW6bu 31.00 USD 2 317568017#20190801050148-0 317568017 1564635708 3072597#1523398724 AVpiMIyE1cnluZ0-K0TA 60.00 USD 1 317568017#20190801050148-1 317568017 1564635708 3072597#1523398724 AVz5wc0H-jtxr-f30F6_ 149.00 USD 9 317568017#20190801050148-2 317568017 1564635708 3072597#1523398724 AVpe7vER1cnluZ0-aJu7 618.00 USD 3 317568018#20190801050317-0 317568018 1564635797 2732808#1517017848 AVpfCQslilAPnD_xThwe 84.00 USD 1 317568018#20190801050317-1 317568018 1564635797 2732808#1517017848 AVpiMIyE1cnluZ0-K0TA 149.00 USD 2 317568019#20190801053142-0 317568019 1564637502 3838589#1546064780 AVpfMVD-ilAPnD_xW6bu 27.00 USD 3 317568019#20190801053149-0 317568019 1564637509 3838589#1546064780 AVpfMVD-ilAPnD_xW6bu 27.00 USD 3 317568019#20190801053149-1 317568019 1564637509 3838589#1546064780 AVpiJoY0LJeJML43iz5- 63.00 USD 1 317568020#20190801053614-0 317568020 1564637774 7159905#1518342898 AVpe7vER1cnluZ0-aJu7 60.00 USD 1 317568020#20190801053614-1 317568020 1564637774 7159905#1518342898 AVpfMVD-ilAPnD_xW6bu 27.00 USD 2 317568021#20190801072018-0 317568021 1564644018 13728809#1537704693 AVpge6k2LJeJML43OhAl 287.00 USD 1 317568021#20190801072018-1 317568021 1564644018 13728809#1537704693 AVpfCW42ilAPnD_xTj0y 102.00 USD 3 317568022#20190801073359-0 317568022 1564644839 8513182#1544320842 AVpfMVD-ilAPnD_xW6bu 27.00 USD 7 317568022#20190801073359-1 317568022 1564644839 8513182#1544320842 AVpjedgc1cnluZ0-W4NI 239.00 USD 3 317568023-0 317568023 1542007#1530946252 AVpf4W5_ilAPnD_xj6lg 887.00 USD 7 317568023-1 317568023 1542007#1530946252 AVpfuJ4pilAPnD_xhDyM 448.00 USD 8 317568024#20190801090823-0 317568024 1564650503 15817754#1515949140 AVpfCmFjLJeJML431EzG 169.00 USD 1 317568024#20190801090823-1 317568024 1564650503 15817754#1515949140 AVpe7V2GLJeJML43yfVz 48.00 USD 10 317568024#20190801090823-2 317568024 1564650503 15817754#1515949140 AVpfDLA0ilAPnD_xT0sq 63.00 USD 3 317568025#20190801091434-0 317568025 1564650874 12537090#1538155776 AVpfm9_AilAPnD_xe8Dd 1799.00 USD 3 317568026#20190801093245-0 317568026 1564651965 19140462#1533611865 AVpffrToLJeJML43-M2g 48.00 USD 7 317568026#20190801093245-1 317568026 1564651965 19140462#1533611865 AVpfCmFjLJeJML431EzG 98.00 USD 3 317568027#20190801102614-0 317568027 1564655174 11935034#1526489741 AVpjedgc1cnluZ0-W4NI 63.00 USD 1 317568027#20190801102614-1 317568027 1564655174 11935034#1526489741 AVpfDLA0ilAPnD_xT0sq 239.00 USD 2 317568028#20190801102711-0 317568028 1564655231 24774688#1515214528 AVpjedgc1cnluZ0-W4NI 287.00 USD 2 317568028#20190801102711-1 317568028 1564655231 24774688#1515214528 AVpfMVD-ilAPnD_xW6bu 27.00 USD 1 317568028#20190801102711-2 317568028 1564655231 24774688#1515214528 AVpfCW42ilAPnD_xTj0y 239.00 USD 3 317568029#20190801113651-0 317568029 1564659411 13721768#1543706725 AVpfeG5oilAPnD_xcTsG 2356.00 USD 2 317568029#20190801113651-1 317568029 1564659411 13721768#1543706725 AVpfZaCp1cnluZ0-kDV9 129.00 USD 3 317568030#20190801114602-0 317568030 1564659962 12744134#1528899571 AVpfIODe1cnluZ0-eg35 218.00 USD 3 317568030#20190801114602-1 317568030 1564659962 12744134#1528899571 AVpjedgc1cnluZ0-W4NI 293.00 USD 1 317568030#20190801114602-2 317568030 1564659962 12744134#1528899571 AVpfdBS41cnluZ0-lBIj 239.00 USD 2 317568031#20190801124333-0 317568031 1564663413 22100013#1524827579 AVpfv62D1cnluZ0-qkPY 184.00 USD 1 317